In this notebook we perform experiments about the capabilities of LLMs of understanding the legality of moves in board games. 

We focus on the board game Chef's Hat (https://whisperproject.eu/chefshat). The rulebook is available at (https://github.com/pablovin/ChefsHatGYM/blob/master/gitImages/RulebookMenuv08.pdf).

In particular, the players have agency only on the first two phases of each round, and most of the decisions take in place during the second phase, which is the focus of this project work.

In this phase, players can either or play a hand of cards; the played cards must be played on top the cards already present on the board, and all of the cards must have the same value, which must be lower than the value of cards on the board. Moreover, it is not possible to play less cards than the amount of cards that are already on the board. Jokers can replace any card when played on the board, and any card can be put on top of them.

# Importing and cleaning data

We begin by creating our dataframe:

In [1]:
import pickle
import pandas as pd
import numpy as np
import torch
import transformers
import torch
import networkx as nx
from transformers import AutoModelForCausalLM, AutoTokenizer, BitsAndBytesConfig  
import random

random_state = 1

random.seed(random_state)

In [2]:
with open('Dataset.pkl', 'rb') as f:
    data = pickle.load(f)

C:\Users\alfio\AppData\Local\Temp\ipykernel_11800\3991492128.py:2: DeprecationWarning: numpy.core.numeric is deprecated and has been renamed to numpy._core.numeric. The numpy._core namespace contains private NumPy internals and its use is discouraged, as NumPy internals can change without warning in any release. In practice, most real-world usage of numpy.core is to access functionality in the public NumPy API. If that is the case, use the public NumPy API. If not, you are using NumPy internals. If you would still like to access an internal attribute, use numpy._core.numeric._frombuffer.
  data = pickle.load(f)


We use the Hamming distance in order to measures (dis)similarity between instances.

In [3]:
def hamming(s1, s2):
    if len(s1) != len(s2):
        raise ValueError("Undefined for sequences of unequal length")
    return sum(ch1 != ch2 for ch1, ch2 in zip(s1, s2))   

In [4]:
def IoU_lists(s1: list[str], s2: list[str]) -> float:
    set1, set2 = set(s1), set(s2)
    return len(set1 & set2) / len(set1 | set2)

We inspect the attributes of the dataset; we will focus only on the "DISCARD" actions.

In [5]:
print(data.columns)
data

Index(['Match', 'Round', 'Agent_Names', 'Source', 'Action_Type',
       'Action_Description', 'Player_Finished', 'Player_Hands', 'Board_Before',
       'Board_After', 'Possible_Actions', 'Current_Roles', 'Match_Score',
       'Game_Score', 'Game_Performance_Score'],
      dtype='object')


Match  Round  \
2024-11-21_15:03:51.314611      0      0   
2024-11-21_15:03:51.314611      1      0   
2024-11-21_15:03:51.315609      1      0   
2024-11-21_15:03:51.327717      1      1   
2024-11-21_15:03:51.336602      1      1   
...                           ...    ...   
2024-11-21_15:06:08.055500    100     26   
2024-11-21_15:06:08.067496    100     26   
2024-11-21_15:06:08.070494    100     26   
2024-11-21_15:06:08.341109    100     26   
2024-11-21_15:06:08.345109    100     26   

                                                             Agent_Names  \
2024-11-21_15:03:51.314611  [RANDOM_01, RANDOM_02, RANDOM_03, RANDOM_04]   
2024-11-21_15:03:51.314611                                           NaN   
2024-11-21_15:03:51.315609                                           NaN   
2024-11-21_15:03:51.327717                                           NaN   
2024-11-21_15:03:51.336602                                           NaN   
...                                                                  ...   
2024-11-21_15:06:08.055500                                           NaN   
2024-11-21_15:06:08.067496                                           NaN   
2024-11-21_15:06:08.070494                                           NaN   
2024-11-21_15:06:08.341109                                           NaN   
2024-11-21_15:06:08.345109                                           NaN   

                               Source       Action_Type Action_Description  \
2024-11-21_15:03:51.314611     SYSTEM  START_EXPERIMENT                NaN   
2024-11-21_15:03:51.314611     SYSTEM         NEW_MATCH                NaN   
2024-11-21_15:03:51.315609     SYSTEM        DEAL_CARDS                NaN   
2024-11-21_15:03:51.327717  RANDOM_01           DISCARD          C11;Q4;J0   
2024-11-21_15:03:51.336602  RANDOM_02           DISCARD               pass   
...                               ...               ...                ...   
2024-11-21_15:06:08.055500  RANDOM_01           DISCARD               pass   
2024-11-21_15:06:08.067496  RANDOM_02           DISCARD           C8;Q1;J0   
2024-11-21_15:06:08.070494  RANDOM_02     DECLARE_PIZZA                NaN   
2024-11-21_15:06:08.341109     SYSTEM         END_MATCH                NaN   
2024-11-21_15:06:08.345109     SYSTEM    END_EXPERIMENT                NaN   

                           Player_Finished  \
2024-11-21_15:03:51.314611             NaN   
2024-11-21_15:03:51.314611             NaN   
2024-11-21_15:03:51.315609             NaN   
2024-11-21_15:03:51.327717             0.0   
2024-11-21_15:03:51.336602           False   
...                                    ...   
2024-11-21_15:06:08.055500           False   
2024-11-21_15:06:08.067496            True   
2024-11-21_15:06:08.070494             NaN   
2024-11-21_15:06:08.341109             NaN   
2024-11-21_15:06:08.345109             NaN   

                                                                 Player_Hands  \
2024-11-21_15:03:51.314611                                                NaN   
2024-11-21_15:03:51.314611                                                NaN   
2024-11-21_15:03:51.315609  [[3, 3, 5, 7, 7, 8, 8, 8, 9, 9, 9, 9, 0, 0, 0,...   
2024-11-21_15:03:51.327717  [0, 0, 0, 0, 3, 3, 5, 7, 7, 8, 8, 8, 9, 9, 9, ...   
2024-11-21_15:03:51.336602  [1, 4, 5, 5, 5, 6, 6, 7, 7, 7, 8, 9, 10, 10, 1...   
...                                                                       ...   
2024-11-21_15:06:08.055500  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
2024-11-21_15:06:08.067496  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
2024-11-21_15:06:08.070494                                                NaN   
2024-11-21_15:06:08.341109                                                NaN   
2024-11-21_15:06:08.345109                                                NaN   

                                                     Board_Before  \
2024-11-21_15:03:51.314611                            

In [6]:
players = data['Agent_Names'][0]
players

C:\Users\alfio\AppData\Local\Temp\ipykernel_11800\3392628886.py:1: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  players = data['Agent_Names'][0]


['RANDOM_01', 'RANDOM_02', 'RANDOM_03', 'RANDOM_04']

In [7]:
data.columns

Index(['Match', 'Round', 'Agent_Names', 'Source', 'Action_Type',
       'Action_Description', 'Player_Finished', 'Player_Hands', 'Board_Before',
       'Board_After', 'Possible_Actions', 'Current_Roles', 'Match_Score',
       'Game_Score', 'Game_Performance_Score'],
      dtype='object')

In [8]:
data_refactored = data[(data['Match'] > 0) & (data['Round'] > 0) & (data['Action_Type'] == 'DISCARD')][['Match', 'Action_Description', 'Player_Hands', 'Board_Before', 'Possible_Actions']]

data_refactored



Match Action_Description  \
2024-11-21_15:03:51.327717      1          C11;Q4;J0   
2024-11-21_15:03:51.336602      1               pass   
2024-11-21_15:03:51.346670      1               pass   
2024-11-21_15:03:51.356687      1          C10;Q4;J0   
2024-11-21_15:03:51.365671      1           C9;Q4;J0   
...                           ...                ...   
2024-11-21_15:06:08.018273    100               pass   
2024-11-21_15:06:08.028495    100               pass   
2024-11-21_15:06:08.036495    100          C10;Q1;J0   
2024-11-21_15:06:08.055500    100               pass   
2024-11-21_15:06:08.067496    100           C8;Q1;J0   

                                                                 Player_Hands  \
2024-11-21_15:03:51.327717  [0, 0, 0, 0, 3, 3, 5, 7, 7, 8, 8, 8, 9, 9, 9, ...   
2024-11-21_15:03:51.336602  [1, 4, 5, 5, 5, 6, 6, 7, 7, 7, 8, 9, 10, 10, 1...   
2024-11-21_15:03:51.346670  [2, 4, 5, 6, 6, 7, 8, 8, 8, 8, 9, 9, 10, 10, 1...   
2024-11-21_15:03:51.356687  [0, 0, 0, 0, 2, 3, 4, 4, 6, 6, 7, 9, 9, 10, 10...   
2024-11-21_15:03:51.365671  [0, 0, 0, 0, 0, 0, 0, 0, 3, 3, 5, 7, 7, 8, 8, ...   
...                                                                       ...   
2024-11-21_15:06:08.018273  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
2024-11-21_15:06:08.028495  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
2024-11-21_15:06:08.036495  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
2024-11-21_15:06:08.055500  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
2024-11-21_15:06:08.067496  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   

                                                     Board_Before  \
2024-11-21_15:03:51.327717     [13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:03:51.336602  [11, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:03:51.346670  [11, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:03:51.356687  [11, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:03:51.365671  [10, 10, 10, 10, 0, 0, 0, 0, 0, 0, 0]   
...                                                           ...   
2024-11-21_15:06:08.018273      [9, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:06:08.028495     [13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:06:08.036495     [13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:06:08.055500     [13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:06:08.067496     [13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   

                                                             Possible_Actions  
2024-11-21_15:03:51.327717  [C11;Q1;J0, C11;Q1;J1, C11;Q2;J0, C11;Q2;J1, C...  
2024-11-21_15:03:51.336602                                             [pass]  
2024-11-21_15:03:51.346670                                   [C8;Q4;J0, pass]  
2024-11-21_15:03:51.356687  [C10;Q3;J1, C10;Q4;J0, C10;Q4;J1, C10;Q5;J0, C...  
2024-11-21_15:03:51.365671     [C8;Q3;J1, C9;Q3;J1, C9;Q4;J0, C9;Q4;J1, pass]  
...                                                                       ...  
2024-11-21_15:06:08.018273                                             [pass]  
2024-11-21_15:06:08.028495                                   [C8;Q1;J0, pass]  
2024-11-21_15:06:08.036495                       [C10;Q1;J0, C11;Q1;J0, pass]  
2024-11-21_15:06:08.055500                                  [C11;Q1;J0, pass]  
2024-11-21_15:06:08.067496                                   [C8;Q1;J0, pass]  

[9844 rows x 5 columns]

In data_refactored, Player_Hands lists the cards that remain in hand AFTER the player has taken the action described in Action_Description.
 
We want to restore the correct player hand so that the Possible_actions column refers to the current player hand and board.

In [9]:
Action_Description_Refactored = data[(data['Match'] > 0) & (data['Round'] > 0) & (data['Action_Type'] == 'DISCARD')]['Action_Description']

New_Action_Description = []

for i in Action_Description_Refactored:
    if i != 'pass':
        actionlist = i.split(';')
    else:
        actionlist = i
    New_Action_Description.append(actionlist)

data_refactored['Action_Description'] = New_Action_Description


In [10]:
Player_Hand_Refactored = []

for i in range(len(data_refactored)):
        newel = list(data_refactored['Player_Hands'][i])
        if data_refactored['Action_Description'][i] != 'pass':
                number = int(data_refactored['Action_Description'][i][0][1:])
                quantity = int(data_refactored['Action_Description'][i][1][1:])
                jolly = int(data_refactored['Action_Description'][i][2][1:])
                for k in range(quantity):
                        newel[newel.index(0)] = number
                for j in range(jolly):
                        newel[newel.index(0)] = 12
        newel.sort(reverse = False)
        newel = [int(i) for i in newel]
        Player_Hand_Refactored.append(newel)

data_refactored['Player_Hands'] = Player_Hand_Refactored
data_refactored

C:\Users\alfio\AppData\Local\Temp\ipykernel_11800\666179860.py:4: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  newel = list(data_refactored['Player_Hands'][i])
C:\Users\alfio\AppData\Local\Temp\ipykernel_11800\666179860.py:5: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  if data_refactored['Action_Description'][i] != 'pass':
C:\Users\alfio\AppData\Local\Temp\ipykernel_11800\666179860.py:6: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]

Match Action_Description  \
2024-11-21_15:03:51.327717      1      [C11, Q4, J0]   
2024-11-21_15:03:51.336602      1               pass   
2024-11-21_15:03:51.346670      1               pass   
2024-11-21_15:03:51.356687      1      [C10, Q4, J0]   
2024-11-21_15:03:51.365671      1       [C9, Q4, J0]   
...                           ...                ...   
2024-11-21_15:06:08.018273    100               pass   
2024-11-21_15:06:08.028495    100               pass   
2024-11-21_15:06:08.036495    100      [C10, Q1, J0]   
2024-11-21_15:06:08.055500    100               pass   
2024-11-21_15:06:08.067496    100       [C8, Q1, J0]   

                                                                 Player_Hands  \
2024-11-21_15:03:51.327717  [3, 3, 5, 7, 7, 8, 8, 8, 9, 9, 9, 9, 11, 11, 1...   
2024-11-21_15:03:51.336602  [1, 4, 5, 5, 5, 6, 6, 7, 7, 7, 8, 9, 10, 10, 1...   
2024-11-21_15:03:51.346670  [2, 4, 5, 6, 6, 7, 8, 8, 8, 8, 9, 9, 10, 10, 1...   
2024-11-21_15:03:51.356687  [2, 3, 4, 4, 6, 6, 7, 9, 9, 10, 10, 10, 10, 10...   
2024-11-21_15:03:51.365671  [0, 0, 0, 0, 3, 3, 5, 7, 7, 8, 8, 8, 9, 9, 9, ...   
...                                                                       ...   
2024-11-21_15:06:08.018273  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
2024-11-21_15:06:08.028495  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
2024-11-21_15:06:08.036495  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
2024-11-21_15:06:08.055500  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
2024-11-21_15:06:08.067496  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   

                                                     Board_Before  \
2024-11-21_15:03:51.327717     [13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:03:51.336602  [11, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:03:51.346670  [11, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:03:51.356687  [11, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:03:51.365671  [10, 10, 10, 10, 0, 0, 0, 0, 0, 0, 0]   
...                                                           ...   
2024-11-21_15:06:08.018273      [9, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:06:08.028495     [13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:06:08.036495     [13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:06:08.055500     [13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
2024-11-21_15:06:08.067496     [13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   

                                                             Possible_Actions  
2024-11-21_15:03:51.327717  [C11;Q1;J0, C11;Q1;J1, C11;Q2;J0, C11;Q2;J1, C...  
2024-11-21_15:03:51.336602                                             [pass]  
2024-11-21_15:03:51.346670                                   [C8;Q4;J0, pass]  
2024-11-21_15:03:51.356687  [C10;Q3;J1, C10;Q4;J0, C10;Q4;J1, C10;Q5;J0, C...  
2024-11-21_15:03:51.365671     [C8;Q3;J1, C9;Q3;J1, C9;Q4;J0, C9;Q4;J1, pass]  
...                                                                       ...  
2024-11-21_15:06:08.018273                                             [pass]  
2024-11-21_15:06:08.028495                                   [C8;Q1;J0, pass]  
2024-11-21_15:06:08.036495                       [C10;Q1;J0, C11;Q1;J0, pass]  
2024-11-21_15:06:08.055500                                  [C11;Q1;J0, pass]  
2024-11-21_15:06:08.067496                                   [C8;Q1;J0, pass]  

[9844 rows x 5 columns]

We now select only the unique pairs of (player_hand, board_state):

In [11]:
data_refactored['Player_Hands'] = data_refactored['Player_Hands'].apply(tuple)
data_refactored['Board_Before'] = data_refactored['Board_Before'].apply(tuple)

data_refactored_unique = data_refactored.drop_duplicates(subset = ['Player_Hands', 'Board_Before'])
data_refactored_unique

Match Action_Description  \
2024-11-21_15:03:51.327717      1      [C11, Q4, J0]   
2024-11-21_15:03:51.336602      1               pass   
2024-11-21_15:03:51.346670      1               pass   
2024-11-21_15:03:51.356687      1      [C10, Q4, J0]   
2024-11-21_15:03:51.365671      1       [C9, Q4, J0]   
...                           ...                ...   
2024-11-21_15:06:07.788984    100               pass   
2024-11-21_15:06:07.856173    100               pass   
2024-11-21_15:06:07.891175    100      [C11, Q1, J0]   
2024-11-21_15:06:07.904180    100      [C11, Q2, J0]   
2024-11-21_15:06:07.942268    100      [C10, Q3, J0]   

                                                                 Player_Hands  \
2024-11-21_15:03:51.327717  (3, 3, 5, 7, 7, 8, 8, 8, 9, 9, 9, 9, 11, 11, 1...   
2024-11-21_15:03:51.336602  (1, 4, 5, 5, 5, 6, 6, 7, 7, 7, 8, 9, 10, 10, 1...   
2024-11-21_15:03:51.346670  (2, 4, 5, 6, 6, 7, 8, 8, 8, 8, 9, 9, 10, 10, 1...   
2024-11-21_15:03:51.356687  (2, 3, 4, 4, 6, 6, 7, 9, 9, 10, 10, 10, 10, 10...   
2024-11-21_15:03:51.365671  (0, 0, 0, 0, 3, 3, 5, 7, 7, 8, 8, 8, 9, 9, 9, ...   
...                                                                       ...   
2024-11-21_15:06:07.788984  (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
2024-11-21_15:06:07.856173  (0, 0, 0, 0, 0, 0, 0, 8, 9, 10, 10, 10, 10, 11...   
2024-11-21_15:06:07.891175  (0, 0, 0, 0, 0, 0, 0, 8, 9, 10, 10, 10, 10, 11...   
2024-11-21_15:06:07.904180  (0, 0, 0, 0, 0, 0, 0, 0, 8, 9, 10, 10, 10, 10,...   
2024-11-21_15:06:07.942268  (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 8, 9, 10, 10...   

                                                     Board_Before  \
2024-11-21_15:03:51.327717     (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:03:51.336602  (11, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:03:51.346670  (11, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:03:51.356687  (11, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:03:51.365671  (10, 10, 10, 10, 0, 0, 0, 0, 0, 0, 0)   
...                                                           ...   
2024-11-21_15:06:07.788984     (10, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:06:07.856173      (7, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:06:07.891175     (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:06:07.904180     (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:06:07.942268     (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   

                                                             Possible_Actions  
2024-11-21_15:03:51.327717  [C11;Q1;J0, C11;Q1;J1, C11;Q2;J0, C11;Q2;J1, C...  
2024-11-21_15:03:51.336602                                             [pass]  
2024-11-21_15:03:51.346670                                   [C8;Q4;J0, pass]  
2024-11-21_15:03:51.356687  [C10;Q3;J1, C10;Q4;J0, C10;Q4;J1, C10;Q5;J0, C...  
2024-11-21_15:03:51.365671     [C8;Q3;J1, C9;Q3;J1, C9;Q4;J0, C9;Q4;J1, pass]  
...                                                                       ...  
2024-11-21_15:06:07.788984                         [C7;Q1;J0, C7;Q2;J0, pass]  
2024-11-21_15:06:07.856173                                             [pass]  
2024-11-21_15:06:07.891175  [C8;Q1;J0, C9;Q1;J0, C10;Q1;J0, C10;Q2;J0, C10...  
2024-11-21_15:06:07.904180  [C8;Q1;J0, C9;Q1;J0, C10;Q1;J0, C10;Q2;J0, C10...  
2024-11-21_15:06:07.942268  [C8;Q1;J0, C9;Q1;J0, C10;Q1;J0, C10;Q2;J0, C10...  

[7819 rows x 5 columns]

In [12]:
data_refactored_unique.iloc[0]['Player_Hands']

(3, 3, 5, 7, 7, 8, 8, 8, 9, 9, 9, 9, 11, 11, 11, 11, 12)

In [13]:
data_refactored_unique

Match Action_Description  \
2024-11-21_15:03:51.327717      1      [C11, Q4, J0]   
2024-11-21_15:03:51.336602      1               pass   
2024-11-21_15:03:51.346670      1               pass   
2024-11-21_15:03:51.356687      1      [C10, Q4, J0]   
2024-11-21_15:03:51.365671      1       [C9, Q4, J0]   
...                           ...                ...   
2024-11-21_15:06:07.788984    100               pass   
2024-11-21_15:06:07.856173    100               pass   
2024-11-21_15:06:07.891175    100      [C11, Q1, J0]   
2024-11-21_15:06:07.904180    100      [C11, Q2, J0]   
2024-11-21_15:06:07.942268    100      [C10, Q3, J0]   

                                                                 Player_Hands  \
2024-11-21_15:03:51.327717  (3, 3, 5, 7, 7, 8, 8, 8, 9, 9, 9, 9, 11, 11, 1...   
2024-11-21_15:03:51.336602  (1, 4, 5, 5, 5, 6, 6, 7, 7, 7, 8, 9, 10, 10, 1...   
2024-11-21_15:03:51.346670  (2, 4, 5, 6, 6, 7, 8, 8, 8, 8, 9, 9, 10, 10, 1...   
2024-11-21_15:03:51.356687  (2, 3, 4, 4, 6, 6, 7, 9, 9, 10, 10, 10, 10, 10...   
2024-11-21_15:03:51.365671  (0, 0, 0, 0, 3, 3, 5, 7, 7, 8, 8, 8, 9, 9, 9, ...   
...                                                                       ...   
2024-11-21_15:06:07.788984  (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
2024-11-21_15:06:07.856173  (0, 0, 0, 0, 0, 0, 0, 8, 9, 10, 10, 10, 10, 11...   
2024-11-21_15:06:07.891175  (0, 0, 0, 0, 0, 0, 0, 8, 9, 10, 10, 10, 10, 11...   
2024-11-21_15:06:07.904180  (0, 0, 0, 0, 0, 0, 0, 0, 8, 9, 10, 10, 10, 10,...   
2024-11-21_15:06:07.942268  (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 8, 9, 10, 10...   

                                                     Board_Before  \
2024-11-21_15:03:51.327717     (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:03:51.336602  (11, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:03:51.346670  (11, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:03:51.356687  (11, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:03:51.365671  (10, 10, 10, 10, 0, 0, 0, 0, 0, 0, 0)   
...                                                           ...   
2024-11-21_15:06:07.788984     (10, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:06:07.856173      (7, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:06:07.891175     (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:06:07.904180     (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:06:07.942268     (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   

                                                             Possible_Actions  
2024-11-21_15:03:51.327717  [C11;Q1;J0, C11;Q1;J1, C11;Q2;J0, C11;Q2;J1, C...  
2024-11-21_15:03:51.336602                                             [pass]  
2024-11-21_15:03:51.346670                                   [C8;Q4;J0, pass]  
2024-11-21_15:03:51.356687  [C10;Q3;J1, C10;Q4;J0, C10;Q4;J1, C10;Q5;J0, C...  
2024-11-21_15:03:51.365671     [C8;Q3;J1, C9;Q3;J1, C9;Q4;J0, C9;Q4;J1, pass]  
...                                                                       ...  
2024-11-21_15:06:07.788984                         [C7;Q1;J0, C7;Q2;J0, pass]  
2024-11-21_15:06:07.856173                                             [pass]  
2024-11-21_15:06:07.891175  [C8;Q1;J0, C9;Q1;J0, C10;Q1;J0, C10;Q2;J0, C10...  
2024-11-21_15:06:07.904180  [C8;Q1;J0, C9;Q1;J0, C10;Q1;J0, C10;Q2;J0, C10...  
2024-11-21_15:06:07.942268  [C8;Q1;J0, C9;Q1;J0, C10;Q1;J0, C10;Q2;J0, C10...  

[7819 rows x 5 columns]

In [14]:
df_train = data_refactored_unique[(data_refactored_unique['Match'] <= 97)]
df_train = df_train#.sample(frac=1, random_state = random_state).reset_index(drop=True) #The other random_states in the .sample() methods shall be left fixed in order to guarantee that the test set remains the same
df_train

Match Action_Description  \
2024-11-21_15:03:51.327717      1      [C11, Q4, J0]   
2024-11-21_15:03:51.336602      1               pass   
2024-11-21_15:03:51.346670      1               pass   
2024-11-21_15:03:51.356687      1      [C10, Q4, J0]   
2024-11-21_15:03:51.365671      1       [C9, Q4, J0]   
...                           ...                ...   
2024-11-21_15:06:04.010495     97       [C5, Q1, J0]   
2024-11-21_15:06:04.048610     97      [C11, Q2, J0]   
2024-11-21_15:06:04.073863     97               pass   
2024-11-21_15:06:04.130421     97      [C10, Q3, J0]   
2024-11-21_15:06:04.144482     97               pass   

                                                                 Player_Hands  \
2024-11-21_15:03:51.327717  (3, 3, 5, 7, 7, 8, 8, 8, 9, 9, 9, 9, 11, 11, 1...   
2024-11-21_15:03:51.336602  (1, 4, 5, 5, 5, 6, 6, 7, 7, 7, 8, 9, 10, 10, 1...   
2024-11-21_15:03:51.346670  (2, 4, 5, 6, 6, 7, 8, 8, 8, 8, 9, 9, 10, 10, 1...   
2024-11-21_15:03:51.356687  (2, 3, 4, 4, 6, 6, 7, 9, 9, 10, 10, 10, 10, 10...   
2024-11-21_15:03:51.365671  (0, 0, 0, 0, 3, 3, 5, 7, 7, 8, 8, 8, 9, 9, 9, ...   
...                                                                       ...   
2024-11-21_15:06:04.010495  (0, 0, 0, 0, 0, 0, 0, 0, 5, 5, 8, 10, 10, 10, ...   
2024-11-21_15:06:04.048610  (0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 8, 10, 10, 10, ...   
2024-11-21_15:06:04.073863  (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 8, 10, 10...   
2024-11-21_15:06:04.130421  (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 8, 10, 10...   
2024-11-21_15:06:04.144482  (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   

                                                     Board_Before  \
2024-11-21_15:03:51.327717     (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:03:51.336602  (11, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:03:51.346670  (11, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:03:51.356687  (11, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:03:51.365671  (10, 10, 10, 10, 0, 0, 0, 0, 0, 0, 0)   
...                                                           ...   
2024-11-21_15:06:04.010495      (6, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:06:04.048610     (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:06:04.073863     (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:06:04.130421     (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)   
2024-11-21_15:06:04.144482   (10, 10, 10, 0, 0, 0, 0, 0, 0, 0, 0)   

                                                             Possible_Actions  
2024-11-21_15:03:51.327717  [C11;Q1;J0, C11;Q1;J1, C11;Q2;J0, C11;Q2;J1, C...  
2024-11-21_15:03:51.336602                                             [pass]  
2024-11-21_15:03:51.346670                                   [C8;Q4;J0, pass]  
2024-11-21_15:03:51.356687  [C10;Q3;J1, C10;Q4;J0, C10;Q4;J1, C10;Q5;J0, C...  
2024-11-21_15:03:51.365671     [C8;Q3;J1, C9;Q3;J1, C9;Q4;J0, C9;Q4;J1, pass]  
...                                                                       ...  
2024-11-21_15:06:04.010495                         [C5;Q1;J0, C5;Q2;J0, pass]  
2024-11-21_15:06:04.048610  [C5;Q1;J0, C8;Q1;J0, C10;Q1;J0, C10;Q2;J0, C10...  
2024-11-21_15:06:04.073863  [C5;Q1;J0, C8;Q1;J0, C10;Q1;J0, C10;Q2;J0, C10...  
2024-11-21_15:06:04.130421  [C8;Q1;J0, C10;Q1;J0, C10;Q2;J0, C10;Q3;J0, C1...  
2024-11-21_15:06:04.144482                                             [pass]  

[7598 rows x 5 columns]

In [15]:
df_test = data_refactored_unique[(data_refactored_unique['Match'] > 97)]

# Experiments

We perform experiments with the Llama-3.1-8B-Instruct model from Huggingface. We adopt 4-bit quantization for improving speed and performances. In all of the experiments we include three settings.

In the first case we do not provide any explanation about the semantics of the input and just ask the model to complete the query based on the provided examples.

In the second case we provide a basic explanation of the input, without references to the rules of the game.

Last, we give a full explanation about the semantics of the input, the rules of the game, and include known techniques of prompt engineering.

We evaluate results according to several metrics: all_moves_accuracy (the fraction of instances for which the full correct list of legal moves is returned), TP (the number of correctly identified legal moves), FP (the number of illegal moves returned), FN (the legal moves which are not returned by the model) and IoU_lists (a variant of Intersection over Union for lists)

In [16]:
model_id = "meta-llama/Meta-Llama-3.1-8B-Instruct"

pipeline = transformers.pipeline(
    "text-generation",
    model=model_id,
    model_kwargs={"torch_dtype": torch.bfloat16,
                  "quantization_config": {"load_in_4bit": True}},
    device_map="cuda:0"
)

Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

Device set to use cuda:0


## Experiment 3: Graph-Based Example Selection

In this last experiment we test the effectiveness of Graph-based example retrieval in the in-context learning setting.

At first, we construct the "training set graph": in this graph nodes are examples from the training set, and edges are constructed between nodes when a similarity score between the examples is greater than a threshold T (or the dissimilarity or distance is below a threshold T).

At test time, for each test instance we extract a subgraph of the constructed larger graph by only selecting nodes that represent examples that are close to the test instance, and returning examples according to a suitable function of the graph (in this case we return the top 5/10/15 nodes according to the PageRank metric (see the notebook for details)).

Note that at inference time there is no need to rebuild the full training set graph; instead it is equivalent and might be more convenient to directly construct the subgraph by only considering the closest nodes to the prompt instance.

Another thing to consider is that for this method to differ from the previous KNN approach, the number of nodes belonging to the extracted subgraph should be (somewhat considerably) greater than 5/10/15 (in general, K) respectively.

### No explanations provided

In [17]:
template = '''You are an expert board game player, and you are playing a card game called Chef’s Hat. This game is played with cards with values ranging from 1 to 13, both included.

In the following examples "A" provides two lists. 
The first list is a description of the cards in hand of a player.
The second list is a description of the cards that are already on the board.

Then "B" replies with the full list of the current legal moves in the situation presented by "A".

Complete the text by listing all the current legal moves given the last description from "A". Only add the text that comes after "B: ".'''

In [18]:
def test(template, nexamples):

    count = 0
    IoU = 0
    TP = 0
    FN = 0
    FP = 0

    for i in range(len(df_test)):

        query = 'A: Player hand: '+ str(df_test.iloc[i]['Player_Hands'])+', Board state: '+str(df_test.iloc[i]['Board_Before'])+'\n'+'B: '

        examples = {}

        for j in range(nexamples):
        # Convert lists to tuples so they can be used as dictionary keys
            key = j
    
        # Hamming distance calculation
            train_data = df_train.iloc[j]['Player_Hands'] + df_train.iloc[j]['Board_Before']
            test_data = df_test.iloc[i]['Player_Hands'] + df_test.iloc[i]['Board_Before']
    
            examples[key] = hamming(train_data, test_data)

        max_hamming = max(examples.values())

        for j in range(nexamples, len(df_train)):
            temp_hamming = hamming(df_train.iloc[j]['Player_Hands'] + df_train.iloc[j]['Board_Before'], df_test.iloc[i]['Player_Hands'] + df_test.iloc[i]['Board_Before'])
            if temp_hamming < max_hamming:
                del examples[max(examples, key=lambda k: examples[k])]
                key = j
                train_data = df_train.iloc[j]['Player_Hands'] + df_train.iloc[j]['Board_Before']
                test_data = df_test.iloc[i]['Player_Hands'] + df_test.iloc[i]['Board_Before']
                examples[key] = hamming(train_data, test_data)
                max_hamming = max(examples.values())



        text_examples = ''

        for el in examples:
            text_examples += 'A: Player hand: '+ str(df_train.iloc[el]['Player_Hands']) + ';\nBoard state: ' + str(df_train.iloc[el]['Board_Before']) + '\n'+'B: ' + str([str(element) for element in df_train.iloc[el]['Possible_Actions']])+'\n\n'

        print('query:\n'+ query,'\n')
        print('retrieved examples:\n\n'+ text_examples,'\n\n')

        messages = [{'role': 'system', 'content': template},{"role": "user", "content": text_examples},{"role": "user", "content": query}]

        outputs = pipeline(
            messages,
            max_new_tokens=500,
            do_sample = False
        )
        #print(outputs[0]['generated_text'][-1]['content'])
        if outputs[0]['generated_text'][-1]['content'][0] == 'B':
            ref_output = outputs[0]['generated_text'][-1]['content'][4:-1].split(sep = ', ')
        else:
            ref_output = outputs[0]['generated_text'][-1]['content'][1:-1].split(sep = ', ')
        final_output = [elem[1:-1] for elem in ref_output]
        print('LLM output:', final_output)
        print('ground truth:', df_test.iloc[i]['Possible_Actions'])
        print(200*'-')

        if final_output == df_test.iloc[i]['Possible_Actions']: #should change to 
            count += 1

        TP_temp = len(set(final_output) & set(df_test.iloc[i]['Possible_Actions']))
        TP += TP_temp
        print('TP:', TP_temp)

        FN_temp = len(set(df_test.iloc[i]['Possible_Actions']) - set(final_output))
        FN += FN_temp
        print('FN:', FN_temp)

        FP_temp = len(set(final_output) - set(df_test.iloc[i]['Possible_Actions']))
        FP += FP_temp
        print('FP:', FP_temp)

        IoU_serv = IoU_lists(final_output, df_test.iloc[i]['Possible_Actions'])
        IoU += IoU_serv
        print('IoU:', IoU_serv,'\n\n')
    
    print('all_moves_accuracy:', count/len(df_test))
    print('Avg. IoU:', IoU/len(df_test))
    print('TP total:', TP)
    print('FP total:', FP)
    print('FN total:', FN)

        


In [19]:
test(template, 5)

C:\Users\alfio\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\transformers\generation\configuration_utils.py:628: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.6` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
C:\Users\alfio\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\transformers\generation\configuration_utils.py:633: UserWarning: `do_sample` is set to `False`. However, `top_p` is set to `0.9` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `top_p`.
  warnings.warn(
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query:
A: Player hand: (2, 3, 5, 5, 5, 6, 6, 9, 9, 9, 10, 11, 11, 11, 11, 12, 12), Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B:  

retrieved examples:

A: Player hand: (4, 4, 5, 5, 6, 6, 6, 6, 9, 10, 10, 11, 11, 11, 11, 12, 12);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C11;Q1;J0', 'C11;Q1;J1', 'C11;Q1;J2', 'C11;Q2;J0', 'C11;Q2;J1', 'C11;Q2;J2', 'C11;Q3;J0', 'C11;Q3;J1', 'C11;Q3;J2', 'C11;Q4;J0', 'C11;Q4;J1', 'C11;Q4;J2', 'pass']

A: Player hand: (2, 5, 5, 7, 8, 8, 8, 9, 9, 9, 10, 11, 11, 11, 11, 12, 12);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C11;Q1;J0', 'C11;Q1;J1', 'C11;Q1;J2', 'C11;Q2;J0', 'C11;Q2;J1', 'C11;Q2;J2', 'C11;Q3;J0', 'C11;Q3;J1', 'C11;Q3;J2', 'C11;Q4;J0', 'C11;Q4;J1', 'C11;Q4;J2', 'pass']

A: Player hand: (2, 3, 3, 4, 5, 6, 7, 8, 9, 9, 10, 11, 11, 11, 11, 11, 12);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C11;Q1;J0', 'C11;Q1;J1', 'C11;Q2;J0', 'C11;Q2;J1', 'C11;Q3;J0', 'C11;Q3;J1', 'C11;Q4;J0', 'C11;Q4;J1', 'C11;Q5;J0', 'C11;Q5;J1

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query:
A: Player hand: (1, 3, 3, 4, 4, 4, 5, 6, 6, 7, 7, 8, 9, 9, 10, 10, 10), Board state: (11, 11, 11, 11, 12, 0, 0, 0, 0, 0, 0)
B:  

retrieved examples:

A: Player hand: (1, 3, 3, 4, 4, 4, 5, 6, 7, 8, 8, 9, 9, 9, 10, 10, 11);
Board state: (12, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: Player hand: (1, 2, 3, 3, 4, 5, 5, 6, 6, 6, 7, 7, 8, 9, 10, 10, 10);
Board state: (11, 11, 11, 11, 11, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: Player hand: (2, 2, 3, 3, 4, 5, 5, 5, 6, 7, 7, 8, 9, 10, 10, 10, 10);
Board state: (11, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0)
B: ['C10;Q4;J0', 'pass']

A: Player hand: (1, 2, 4, 4, 4, 5, 5, 6, 6, 8, 8, 9, 9, 9, 10, 10, 10);
Board state: (11, 11, 11, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C4;Q3;J0', 'C9;Q3;J0', 'C10;Q3;J0', 'pass']

A: Player hand: (2, 3, 3, 4, 4, 4, 5, 5, 6, 7, 7, 8, 8, 9, 10, 10, 10);
Board state: (11, 12, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q2;J0', 'C4;Q2;J0', 'C4;Q3;J0', 'C5;Q2;J0', 'C7;Q2;J0', 'C8;Q2;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'pass']

 


LLM output:

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


...

query:
A: Player hand: (0, 0, 0, 0, 0, 0, 0, 8, 9, 10, 10, 10, 10, 11, 11, 11, 11), Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B:  

retrieved examples:

A: Player hand: (0, 0, 0, 0, 0, 0, 6, 6, 9, 9, 10, 10, 10, 11, 11, 11, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C6;Q1;J0', 'C6;Q2;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'C11;Q4;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 6, 6, 10, 10, 10, 11, 11, 11, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C6;Q1;J0', 'C6;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'C11;Q4;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 6, 8, 9, 10, 10, 10, 10, 10, 11, 11, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C6;Q1;J0', 'C8;Q1;J0', 'C9;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C10;Q5;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query:
A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 8, 9, 10, 10, 10, 10, 11, 11, 11), Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B:  

retrieved examples:

A: Player hand: (0, 0, 0, 0, 0, 0, 7, 8, 8, 9, 10, 10, 10, 10, 11, 11, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C7;Q1;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C9;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 9, 10, 10, 10, 10, 10, 11, 11, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C9;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C10;Q5;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 5, 9, 10, 10, 10, 11, 11, 11, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C5;Q1;J0', 'C9;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'C11;Q4;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 6, 8, 9, 10, 10, 10, 1

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query:
A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 8, 9, 10, 10, 10, 10), Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B:  

retrieved examples:

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 10);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 8, 9, 9, 9, 10, 10);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C8;Q1;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C9;Q3;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 8, 8, 9, 10, 10, 10, 10);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C8;Q1;J0', 'C8;Q2;J0', 'C9;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 9, 10, 10, 10, 10);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C5;Q1;J0', 'C9;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'pass']

A: Player hand: (0, 0

In [20]:
test(template, 10)

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query:
A: Player hand: (2, 3, 5, 5, 5, 6, 6, 9, 9, 9, 10, 11, 11, 11, 11, 12, 12), Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B:  

retrieved examples:

A: Player hand: (4, 4, 5, 5, 6, 6, 6, 6, 9, 10, 10, 11, 11, 11, 11, 12, 12);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C11;Q1;J0', 'C11;Q1;J1', 'C11;Q1;J2', 'C11;Q2;J0', 'C11;Q2;J1', 'C11;Q2;J2', 'C11;Q3;J0', 'C11;Q3;J1', 'C11;Q3;J2', 'C11;Q4;J0', 'C11;Q4;J1', 'C11;Q4;J2', 'pass']

A: Player hand: (3, 3, 4, 5, 7, 8, 8, 8, 9, 9, 10, 11, 11, 11, 11, 11, 12);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C11;Q1;J0', 'C11;Q1;J1', 'C11;Q2;J0', 'C11;Q2;J1', 'C11;Q3;J0', 'C11;Q3;J1', 'C11;Q4;J0', 'C11;Q4;J1', 'C11;Q5;J0', 'C11;Q5;J1', 'pass']

A: Player hand: (2, 5, 5, 7, 8, 8, 8, 9, 9, 9, 10, 11, 11, 11, 11, 12, 12);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C11;Q1;J0', 'C11;Q1;J1', 'C11;Q1;J2', 'C11;Q2;J0', 'C11;Q2;J1', 'C11;Q2;J2', 'C11;Q3;J0', 'C11;Q3;J1', 'C11;Q3;J2', 'C11;Q4;J0', 'C11;Q4;J1', 'C11;Q4;J2

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query:
A: Player hand: (1, 3, 3, 4, 4, 4, 5, 6, 6, 7, 7, 8, 9, 9, 10, 10, 10), Board state: (11, 11, 11, 11, 12, 0, 0, 0, 0, 0, 0)
B:  

retrieved examples:

A: Player hand: (1, 3, 3, 4, 4, 4, 5, 6, 7, 8, 8, 9, 9, 9, 10, 10, 11);
Board state: (12, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: Player hand: (1, 2, 3, 3, 4, 5, 5, 6, 6, 6, 7, 7, 8, 9, 10, 10, 10);
Board state: (11, 11, 11, 11, 11, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: Player hand: (2, 2, 3, 3, 4, 5, 5, 5, 6, 7, 7, 8, 9, 10, 10, 10, 10);
Board state: (11, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0)
B: ['C10;Q4;J0', 'pass']

A: Player hand: (1, 2, 4, 4, 4, 6, 6, 6, 7, 7, 7, 8, 8, 9, 9, 10, 10);
Board state: (11, 11, 11, 12, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: Player hand: (1, 2, 3, 4, 4, 4, 6, 6, 7, 7, 7, 7, 9, 9, 9, 10, 10);
Board state: (11, 12, 11, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C4;Q3;J0', 'C7;Q3;J0', 'C7;Q4;J0', 'C9;Q3;J0', 'pass']

A: Player hand: (1, 2, 3, 4, 4, 5, 6, 7, 7, 7, 8, 8, 8, 9, 9, 10, 10);
Board state: (11, 11, 11, 12, 1

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


...

query:
A: Player hand: (0, 0, 0, 0, 0, 0, 0, 8, 9, 10, 10, 10, 10, 11, 11, 11, 11), Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B:  

retrieved examples:

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 7, 10, 10, 10, 11, 11, 11, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C7;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'C11;Q4;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 8, 8, 9, 10, 10, 11, 11, 11, 11, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C8;Q1;J0', 'C8;Q2;J0', 'C9;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'C11;Q4;J0', 'C11;Q5;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 6, 6, 9, 9, 10, 10, 10, 11, 11, 11, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C6;Q1;J0', 'C6;Q2;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'C11;Q4;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 6, 6, 10, 10, 10, 11

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query:
A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 8, 9, 10, 10, 10, 10, 11, 11, 11), Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B:  

retrieved examples:

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 8, 9, 9, 10, 10, 10, 10, 11, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C8;Q1;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 7, 8, 8, 9, 10, 10, 10, 10, 11, 11, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C7;Q1;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C9;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 9, 10, 10, 10, 10, 10, 11, 11, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C9;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C10;Q5;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 5, 9, 10, 10, 10, 11,

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query:
A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 8, 9, 10, 10, 10, 10), Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B:  

retrieved examples:

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 10);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 8, 9, 9, 9, 10, 10);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C8;Q1;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C9;Q3;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 4, 6, 8, 9, 10, 10, 10, 10);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C4;Q1;J0', 'C6;Q1;J0', 'C8;Q1;J0', 'C9;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 8, 8, 9, 10, 10, 10, 10);
Board state: (3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 8, 8, 9, 10, 10, 10, 10);
Board state: 

In [21]:
test(template, 15)

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query:
A: Player hand: (2, 3, 5, 5, 5, 6, 6, 9, 9, 9, 10, 11, 11, 11, 11, 12, 12), Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B:  

retrieved examples:

A: Player hand: (4, 4, 5, 5, 6, 6, 6, 6, 9, 10, 10, 11, 11, 11, 11, 12, 12);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C11;Q1;J0', 'C11;Q1;J1', 'C11;Q1;J2', 'C11;Q2;J0', 'C11;Q2;J1', 'C11;Q2;J2', 'C11;Q3;J0', 'C11;Q3;J1', 'C11;Q3;J2', 'C11;Q4;J0', 'C11;Q4;J1', 'C11;Q4;J2', 'pass']

A: Player hand: (3, 3, 4, 5, 7, 8, 8, 8, 9, 9, 10, 11, 11, 11, 11, 11, 12);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C11;Q1;J0', 'C11;Q1;J1', 'C11;Q2;J0', 'C11;Q2;J1', 'C11;Q3;J0', 'C11;Q3;J1', 'C11;Q4;J0', 'C11;Q4;J1', 'C11;Q5;J0', 'C11;Q5;J1', 'pass']

A: Player hand: (2, 5, 5, 7, 8, 8, 8, 9, 9, 9, 10, 11, 11, 11, 11, 12, 12);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C11;Q1;J0', 'C11;Q1;J1', 'C11;Q1;J2', 'C11;Q2;J0', 'C11;Q2;J1', 'C11;Q2;J2', 'C11;Q3;J0', 'C11;Q3;J1', 'C11;Q3;J2', 'C11;Q4;J0', 'C11;Q4;J1', 'C11;Q4;J2

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query:
A: Player hand: (1, 3, 3, 4, 4, 4, 5, 6, 6, 7, 7, 8, 9, 9, 10, 10, 10), Board state: (11, 11, 11, 11, 12, 0, 0, 0, 0, 0, 0)
B:  

retrieved examples:

A: Player hand: (1, 3, 3, 4, 4, 4, 5, 6, 7, 8, 8, 9, 9, 9, 10, 10, 11);
Board state: (12, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: Player hand: (1, 2, 3, 3, 4, 5, 5, 6, 6, 6, 7, 7, 8, 9, 10, 10, 10);
Board state: (11, 11, 11, 11, 11, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: Player hand: (0, 0, 0, 0, 0, 4, 5, 5, 6, 6, 7, 8, 9, 9, 10, 10, 10);
Board state: (11, 11, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C5;Q2;J0', 'C6;Q2;J0', 'C9;Q2;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'pass']

A: Player hand: (2, 2, 3, 3, 4, 5, 5, 5, 6, 7, 7, 8, 9, 10, 10, 10, 10);
Board state: (11, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0)
B: ['C10;Q4;J0', 'pass']

A: Player hand: (1, 3, 3, 4, 5, 5, 6, 7, 7, 8, 8, 8, 8, 9, 9, 10, 10);
Board state: (11, 11, 11, 11, 12, 12, 0, 0, 0, 0, 0)
B: ['pass']

A: Player hand: (1, 2, 4, 4, 4, 6, 6, 6, 7, 7, 7, 8, 8, 9, 9, 10, 10);
Board state: (1

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


...

query:
A: Player hand: (0, 0, 0, 0, 0, 0, 0, 8, 9, 10, 10, 10, 10, 11, 11, 11, 11), Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B:  

retrieved examples:

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 7, 10, 10, 10, 11, 11, 11, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C7;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'C11;Q4;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 8, 8, 9, 10, 10, 11, 11, 11, 11, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C8;Q1;J0', 'C8;Q2;J0', 'C9;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'C11;Q4;J0', 'C11;Q5;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 6, 6, 9, 9, 10, 10, 10, 11, 11, 11, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C6;Q1;J0', 'C6;Q2;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'C11;Q4;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 6, 6, 10, 10, 10, 11

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query:
A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 8, 9, 10, 10, 10, 10, 11, 11, 11), Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B:  

retrieved examples:

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 8, 9, 9, 10, 10, 10, 10, 11, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C8;Q1;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 7, 8, 8, 9, 10, 10, 10, 10, 11, 11, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C7;Q1;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C9;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 8, 8, 9, 10, 10, 11, 11, 11, 11, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C8;Q1;J0', 'C8;Q2;J0', 'C9;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'C11;Q4;J0', 'C11;Q5;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 9, 10, 10, 

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query:
A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 8, 9, 10, 10, 10, 10), Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B:  

retrieved examples:

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 8, 9, 9, 10, 10, 10);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C5;Q1;J0', 'C8;Q1;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 8, 8, 10, 10, 10, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C8;Q1;J0', 'C8;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C11;Q1;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 10);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 8, 9, 9, 9, 10, 10);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C8;Q1;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C9;Q3;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'pass']

A: Player hand: (0, 0, 

In [22]:
test(template, 30)

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query:
A: Player hand: (2, 3, 5, 5, 5, 6, 6, 9, 9, 9, 10, 11, 11, 11, 11, 12, 12), Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B:  

retrieved examples:

A: Player hand: (3, 3, 4, 6, 7, 7, 8, 9, 9, 10, 10, 11, 11, 11, 11, 11, 12);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q1;J0', 'C3;Q1;J1', 'C3;Q2;J0', 'C3;Q2;J1', 'C4;Q1;J0', 'C4;Q1;J1', 'C6;Q1;J0', 'C6;Q1;J1', 'C7;Q1;J0', 'C7;Q1;J1', 'C7;Q2;J0', 'C7;Q2;J1', 'C8;Q1;J0', 'C8;Q1;J1', 'C9;Q1;J0', 'C9;Q1;J1', 'C9;Q2;J0', 'C9;Q2;J1', 'C10;Q1;J0', 'C10;Q1;J1', 'C10;Q2;J0', 'C10;Q2;J1', 'C11;Q1;J0', 'C11;Q1;J1', 'C11;Q2;J0', 'C11;Q2;J1', 'C11;Q3;J0', 'C11;Q3;J1', 'C11;Q4;J0', 'C11;Q4;J1', 'C11;Q5;J0', 'C11;Q5;J1', 'C0;Q0;J1', 'pass']

A: Player hand: (4, 4, 5, 5, 6, 6, 6, 6, 9, 10, 10, 11, 11, 11, 11, 12, 12);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C11;Q1;J0', 'C11;Q1;J1', 'C11;Q1;J2', 'C11;Q2;J0', 'C11;Q2;J1', 'C11;Q2;J2', 'C11;Q3;J0', 'C11;Q3;J1', 'C11;Q3;J2', 'C11;Q4;J0', 'C11;Q4;J1', 'C11;Q4;J2', 'pass']



Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query:
A: Player hand: (1, 3, 3, 4, 4, 4, 5, 6, 6, 7, 7, 8, 9, 9, 10, 10, 10), Board state: (11, 11, 11, 11, 12, 0, 0, 0, 0, 0, 0)
B:  

retrieved examples:

A: Player hand: (1, 3, 3, 4, 4, 4, 5, 6, 7, 8, 8, 9, 9, 9, 10, 10, 11);
Board state: (12, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: Player hand: (1, 3, 3, 4, 4, 4, 5, 6, 7, 8, 8, 9, 9, 9, 10, 10, 11);
Board state: (8, 8, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q2;J0', 'C4;Q2;J0', 'C4;Q3;J0', 'pass']

A: Player hand: (1, 3, 3, 4, 4, 4, 5, 6, 7, 8, 8, 9, 9, 9, 10, 10, 11);
Board state: (2, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: Player hand: (1, 3, 3, 4, 4, 4, 5, 6, 7, 8, 8, 9, 9, 9, 10, 10, 11);
Board state: (7, 7, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q2;J0', 'C4;Q2;J0', 'C4;Q3;J0', 'pass']

A: Player hand: (1, 3, 3, 4, 4, 4, 5, 6, 7, 8, 8, 9, 9, 9, 10, 10, 11);
Board state: (10, 10, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q2;J0', 'C4;Q2;J0', 'C4;Q3;J0', 'C8;Q2;J0', 'C9;Q2;J0', 'C9;Q3;J0', 'pass']

A: Player hand: (1, 2, 3, 3, 4, 

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


...

query:
A: Player hand: (0, 0, 0, 0, 0, 0, 0, 8, 9, 10, 10, 10, 10, 11, 11, 11, 11), Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B:  

retrieved examples:

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 11, 11, 11, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'C11;Q4;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 7, 10, 10, 10, 11, 11, 11, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C7;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'C11;Q4;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 8, 8, 9, 10, 10, 11, 11, 11, 11, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C8;Q1;J0', 'C8;Q2;J0', 'C9;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'C11;Q4;J0', 'C11;Q5;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 7, 9, 10, 10, 10, 10, 10, 10, 11, 11, 11, 11);
Board state: (13, 0, 0, 0, 0, 

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query:
A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 8, 9, 10, 10, 10, 10, 11, 11, 11), Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B:  

retrieved examples:

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 8, 9, 9, 10, 10, 10, 10, 11, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C8;Q1;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 7, 7, 10, 10, 10, 10, 11, 11, 11);
Board state: (3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 7, 8, 8, 9, 10, 10, 10, 10, 11, 11, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C7;Q1;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C9;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 6, 7, 8, 9, 9, 10, 10, 10, 11, 11, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C6;Q1;J0', 'C7;Q1;J0', 'C8;Q1;J0', 'C9;Q1;J0', 'C9;Q

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query:
A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 8, 9, 10, 10, 10, 10), Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B:  

retrieved examples:

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 8, 8, 10, 10, 10, 10);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q1;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 8, 9, 9, 10, 10, 10);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C5;Q1;J0', 'C8;Q1;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 8, 8, 10, 10, 10, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C8;Q1;J0', 'C8;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C11;Q1;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 10);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'pass']

A: Play

In [23]:
test(template, 50)

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query:
A: Player hand: (2, 3, 5, 5, 5, 6, 6, 9, 9, 9, 10, 11, 11, 11, 11, 12, 12), Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B:  

retrieved examples:

A: Player hand: (3, 3, 4, 6, 7, 7, 8, 9, 9, 10, 10, 11, 11, 11, 11, 11, 12);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q1;J0', 'C3;Q1;J1', 'C3;Q2;J0', 'C3;Q2;J1', 'C4;Q1;J0', 'C4;Q1;J1', 'C6;Q1;J0', 'C6;Q1;J1', 'C7;Q1;J0', 'C7;Q1;J1', 'C7;Q2;J0', 'C7;Q2;J1', 'C8;Q1;J0', 'C8;Q1;J1', 'C9;Q1;J0', 'C9;Q1;J1', 'C9;Q2;J0', 'C9;Q2;J1', 'C10;Q1;J0', 'C10;Q1;J1', 'C10;Q2;J0', 'C10;Q2;J1', 'C11;Q1;J0', 'C11;Q1;J1', 'C11;Q2;J0', 'C11;Q2;J1', 'C11;Q3;J0', 'C11;Q3;J1', 'C11;Q4;J0', 'C11;Q4;J1', 'C11;Q5;J0', 'C11;Q5;J1', 'C0;Q0;J1', 'pass']

A: Player hand: (3, 4, 6, 6, 6, 7, 8, 9, 9, 9, 10, 10, 11, 11, 11, 11, 12);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q1;J0', 'C3;Q1;J1', 'C4;Q1;J0', 'C4;Q1;J1', 'C6;Q1;J0', 'C6;Q1;J1', 'C6;Q2;J0', 'C6;Q2;J1', 'C6;Q3;J0', 'C6;Q3;J1', 'C7;Q1;J0', 'C7;Q1;J1', 'C8;Q1;J0', 'C8;Q1;J1'

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query:
A: Player hand: (1, 3, 3, 4, 4, 4, 5, 6, 6, 7, 7, 8, 9, 9, 10, 10, 10), Board state: (11, 11, 11, 11, 12, 0, 0, 0, 0, 0, 0)
B:  

retrieved examples:

A: Player hand: (1, 3, 4, 5, 6, 6, 6, 7, 7, 8, 8, 9, 9, 9, 10, 10, 10);
Board state: (11, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: Player hand: (1, 3, 3, 4, 4, 4, 5, 6, 7, 8, 8, 9, 9, 9, 10, 10, 11);
Board state: (12, 11, 11, 11, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: Player hand: (1, 3, 3, 4, 4, 4, 5, 6, 7, 8, 8, 9, 9, 9, 10, 10, 11);
Board state: (8, 8, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q2;J0', 'C4;Q2;J0', 'C4;Q3;J0', 'pass']

A: Player hand: (1, 3, 3, 4, 4, 4, 5, 6, 7, 8, 8, 9, 9, 9, 10, 10, 11);
Board state: (2, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['pass']

A: Player hand: (1, 3, 3, 4, 4, 4, 5, 6, 7, 8, 8, 9, 9, 9, 10, 10, 11);
Board state: (7, 7, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q2;J0', 'C4;Q2;J0', 'C4;Q3;J0', 'pass']

A: Player hand: (1, 3, 3, 4, 4, 4, 5, 6, 7, 8, 8, 9, 9, 9, 10, 10, 11);
Board state: (10, 10, 0, 0, 0,

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


...

query:
A: Player hand: (0, 0, 0, 0, 0, 0, 0, 8, 9, 10, 10, 10, 10, 11, 11, 11, 11), Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B:  

retrieved examples:

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 11, 11, 11, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'C11;Q4;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 7, 10, 10, 10, 11, 11, 11, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C7;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'C11;Q4;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 4, 7, 8, 10, 10, 11, 11, 11, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C4;Q1;J0', 'C7;Q1;J0', 'C8;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'C11;Q4;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 7, 8, 8, 9, 10, 10, 10, 10, 11, 11, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query:
A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 8, 9, 10, 10, 10, 10, 11, 11, 11), Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B:  

retrieved examples:

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 8, 9, 9, 10, 10, 10, 10, 11, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C8;Q1;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 7, 10, 10, 10, 11, 11, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C5;Q1;J0', 'C7;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 2, 7, 8, 10, 10, 10, 10, 11, 11, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C2;Q1;J0', 'C7;Q1;J0', 'C8;Q1;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'C11;Q1;J0', 'C11;Q2;J0', 'C11;Q3;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 7, 7, 8, 10, 10, 10, 11, 11, 11);
Board state: (1

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


query:
A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 8, 9, 10, 10, 10, 10), Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B:  

retrieved examples:

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 8, 8, 10, 10, 10, 10);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C3;Q1;J0', 'C8;Q1;J0', 'C8;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 8, 9, 9, 10, 10, 10);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C5;Q1;J0', 'C8;Q1;J0', 'C9;Q1;J0', 'C9;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 8, 8, 10, 10, 10, 11);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C8;Q1;J0', 'C8;Q2;J0', 'C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C11;Q1;J0', 'pass']

A: Player hand: (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 10, 10, 10);
Board state: (13, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
B: ['C10;Q1;J0', 'C10;Q2;J0', 'C10;Q3;J0', 'C10;Q4;J0', 'pass']

A: Play